# Downloading  Data

In [2]:
import os
import urllib

In [3]:
BASE_DIR = "/dbfs/FileStore/tables"
listing_zip = os.path.join(BASE_DIR, "listings.csv.gz")
reviews_zip = os.path.join(BASE_DIR, "reviews.csv.gz")
neighbourhoods_csv = os.path.join(BASE_DIR, "neighbourhoods.csv")

In [4]:
# Downloading from the URL. Two files will be in zip format while one will be CSV.
urllib.request.urlretrieve("http://data.insideairbnb.com/united-states/ny/new-york-city/2020-03-13/data/listings.csv.gz", listing_zip)
urllib.request.urlretrieve("http://data.insideairbnb.com/united-states/ny/new-york-city/2020-03-13/data/reviews.csv.gz", reviews_zip)
urllib.request.urlretrieve("http://data.insideairbnb.com/united-states/ny/new-york-city/2020-03-13/visualisations/neighbourhoods.csv", neighbourhoods_csv)

Out[4]: ('/dbfs/FileStore/tables/neighbourhoods.csv',
 <http.client.HTTPMessage at 0x7f9b486ed278>)

In [5]:
%sh
gunzip /dbfs/FileStore/tables/listings.csv.gz
gunzip /dbfs/FileStore/tables/reviews.csv.gz

# Part 1 - Loading and saving Data

In [7]:
# File location and type
file_location = "/FileStore/tables/listings.csv"
file_type = "csv"

# CSV options
infer_schema = "true"
first_row_is_header = "true"
delimiter = ","

# The applied options are for CSV files. For other file types, these will be ignored.
df_listing = spark.read.format(file_type) \
  .option("inferSchema", infer_schema) \
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load(file_location)

display(df_listing)

id listing_url scrape_id last_scraped name summary space description experiences_offered neighborhood_overview notes transit access interaction house_rules thumbnail_url medium_url picture_url xl_picture_url host_id host_url host_name host_since host_location host_about host_response_time host_response_rate host_acceptance_rate host_is_superhost host_thumbnail_url host_picture_url host_neighbourhood host_listings_count host_total_listings_count host_verifications host_has_profile_pic host_identity_verified street neighbourhood neighbourhood_cleansed neighbourhood_group_cleansed city state zipcode market smart_location country_code country latitude longitude is_location_exact property_type room_type accommodates bathrooms bedrooms beds bed_type amenities square_feet price weekly_price monthly_price security_deposit cleaning_fee guests_included extra_people minimum_nights maximum_nights minimum_minimum_nights maximum_minimum_nights minimum_maximum_nights maximum_maximum_nights minimum_nights_avg_ntm maximum_nights_avg_ntm calendar_updated has_availability availability_30 availability_60 availability_90 availability_365 calendar_last_scraped number_of_reviews number_of_reviews_ltm first_review last_review review_scores_rating review_scores_accuracy review_scores_cleanliness review_scores_checkin review_scores_communication review_scores_location review_scores_value requires_license license jurisdiction_names instant_bookable is_business_travel_ready cancellation_policy require_guest_profile_picture require_guest_phone_verification calculated_host_listings_count calculated_host_listings_count_entire_homes calculated_host_listings_count_private_rooms calculated_host_listings_count_shared_rooms reviews_per_month 2060 https://www.airbnb.com/rooms/2060 20200313233810 2020-03-14 Modern NYC null Lovely, spacious, sunny 1 BR apartment in 6th Floor elevator building steps from gorgeous Fort Tryon Park/The Cloisters in Manhattan, less than 5 min walk from the A-train, 25-minutes to midtown Manhattan. Neighborhood is quiet, safe and hilly. Fully equipped, all brand new kitchen; king size bed; WiFi and cable; and more. We are looking for responsible renters who don't mind feeding our Maine Coon cat while staying there. Lovely, spacious, sunny 1 BR apartment in 6th Floor elevator building steps from gorgeous Fort Tryon Park/The Cloisters in Manhattan, less than 5 min walk from the A-train, 25-minutes to midtown Manhattan. Neighborhood is quiet, safe and hilly. Fully equipped, all brand new kitchen; king size bed; WiFi and cable; and more. We are looking for responsible renters who don't mind feeding our Maine Coon cat while staying there. none null null null null null null null null https://a0.muscache.com/im/pictures/3755/3f9d31cf_original.jpg?aki_policy=large null 2259 https://www.airbnb.com/users/show/2259 Jenny 2008-08-18 US null a few days or more 22% 50% f https://a0.muscache.com/im/users/2259/profile_pic/1259094383/original.jpg?aki_policy=profile_small https://a0.muscache.com/im/users/2259/profile_pic/1259094383/original.jpg?aki_policy=profile_x_medium Washington Heights 0 0 ['reviews'] t f New York, NY, United States Manhattan Washington Heights Manhattan New York NY 10040 New York New York, NY US United States 40.85722 -73.9379 t Other Private room 2 null 1 2 Real Bed {Internet,Wifi} null $100.00 null null null null 1 $0.00 1 730 1 1 730 730 1.0 730.0 4 weeks ago t 30 60 90 365 2020-03-14 1 0 2008-09-22 2008-09-22 80 null null null null null null f null null f f flexible f f 1 0 1 0 0.01 2595 https://www.airbnb.com/rooms/2595 20200313233810 2020-03-14 Skylit Midtown Castle Beautiful, spacious skylit studio in the heart of Midtown, Manhattan. STUNNING SKYLIT STUDIO / 1 BED + SINGLE / FULL BATH / FULL KITCHEN / FIREPLACE / CENTRALLY LOCATED / WiFi + APPLE TV / SHEETS + TOWELS - Spacious (500+ft²), immaculate and nicely furnished & designed studio. - Tuck yourself into the ultra comfortable bed under the skylight. Fall in love with a my

This data has some **problem**. For example

In [9]:
df_listing.select("id").show(4)

+--------------------+
 id|
+--------------------+
 2060|
 2595|
I am a Sound Ther...|
 3831|
+--------------------+
only showing top 4 rows

As you can see that ID in third row is a string which is not possible.

Furthermore, look at this

In [11]:
df_listing.select("host_about").show(5)

+--------------------+
 host_about|
+--------------------+
 null|
A New Yorker sinc...|
 10018|
 2008-12-07|
I'm an artist, wr...|
+--------------------+
only showing top 5 rows

Now this, host_about column should be a discription of the host and not some integer or date as given in 3rd and 4th row.

Reason for issue: This data has text which is having newline characters (Enter). Now by default newline character in a CSV will
be considered as a new row of the data. This habit is causing problem. We can solve it by using multiline=True as below.

In [13]:
# File location and type
file_location = "/FileStore/tables/listings.csv"
file_type = "csv"

# CSV options
infer_schema = "true"
first_row_is_header = "true"
delimiter = ","

# The applied options are for CSV files. For other file types, these will be ignored.
df_listing = spark.read.format(file_type) \
  .option("multiline", "true") \
  .option("inferSchema", infer_schema) \
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load(file_location)

display(df_listing)

id listing_url scrape_id last_scraped name summary space description experiences_offered neighborhood_overview notes transit access interaction house_rules thumbnail_url medium_url picture_url xl_picture_url host_id host_url host_name host_since host_location host_about host_response_time host_response_rate host_acceptance_rate host_is_superhost host_thumbnail_url host_picture_url host_neighbourhood host_listings_count host_total_listings_count host_verifications host_has_profile_pic host_identity_verified street neighbourhood neighbourhood_cleansed neighbourhood_group_cleansed city state zipcode market smart_location country_code country latitude longitude is_location_exact property_type room_type accommodates bathrooms bedrooms beds bed_type amenities square_feet price weekly_price monthly_price security_deposit cleaning_fee guests_included extra_people minimum_nights maximum_nights minimum_minimum_nights maximum_minimum_nights minimum_maximum_nights maximum_maximum_nights minimum_nights_avg_ntm maximum_nights_avg_ntm calendar_updated has_availability availability_30 availability_60 availability_90 availability_365 calendar_last_scraped number_of_reviews number_of_reviews_ltm first_review last_review review_scores_rating review_scores_accuracy review_scores_cleanliness review_scores_checkin review_scores_communication review_scores_location review_scores_value requires_license license jurisdiction_names instant_bookable is_business_travel_ready cancellation_policy require_guest_profile_picture require_guest_phone_verification calculated_host_listings_count calculated_host_listings_count_entire_homes calculated_host_listings_count_private_rooms calculated_host_listings_count_shared_rooms reviews_per_month 2060 https://www.airbnb.com/rooms/2060 20200313233810 2020-03-14 Modern NYC null Lovely, spacious, sunny 1 BR apartment in 6th Floor elevator building steps from gorgeous Fort Tryon Park/The Cloisters in Manhattan, less than 5 min walk from the A-train, 25-minutes to midtown Manhattan. Neighborhood is quiet, safe and hilly. Fully equipped, all brand new kitchen; king size bed; WiFi and cable; and more. We are looking for responsible renters who don't mind feeding our Maine Coon cat while staying there. Lovely, spacious, sunny 1 BR apartment in 6th Floor elevator building steps from gorgeous Fort Tryon Park/The Cloisters in Manhattan, less than 5 min walk from the A-train, 25-minutes to midtown Manhattan. Neighborhood is quiet, safe and hilly. Fully equipped, all brand new kitchen; king size bed; WiFi and cable; and more. We are looking for responsible renters who don't mind feeding our Maine Coon cat while staying there. none null null null null null null null null https://a0.muscache.com/im/pictures/3755/3f9d31cf_original.jpg?aki_policy=large null 2259 https://www.airbnb.com/users/show/2259 Jenny 2008-08-18 US null a few days or more 22% 50% f https://a0.muscache.com/im/users/2259/profile_pic/1259094383/original.jpg?aki_policy=profile_small https://a0.muscache.com/im/users/2259/profile_pic/1259094383/original.jpg?aki_policy=profile_x_medium Washington Heights 0 0 ['reviews'] t f New York, NY, United States Manhattan Washington Heights Manhattan New York NY 10040 New York New York, NY US United States 40.85722 -73.9379 t Other Private room 2 null 1 2 Real Bed {Internet,Wifi} null $100.00 null null null null 1 $0.00 1 730 1 1 730 730 1.0 730.0 4 weeks ago t 30 60 90 365 2020-03-14 1 0 2008-09-22 2008-09-22 80 null null null null null null f null null f f flexible f f 1 0 1 0 0.01 2595 https://www.airbnb.com/rooms/2595 20200313233810 2020-03-14 Skylit Midtown Castle Beautiful, spacious skylit studio in the heart of Midtown, Manhattan. STUNNING SKYLIT STUDIO / 1 BED + SINGLE / FULL BATH / FULL KITCHEN / FIREPLACE / CENTRALLY LOCATED / WiFi + APPLE TV / SHEETS + TOWELS - Spacious (500+ft²), immaculate and nicely furnished & designed studio. - Tuck yourself into the ultra comfortable bed under the skylight. Fall in love with a my

Let us look at the data now

In [15]:
df_listing.select("id", "host_about", "host_since").show()

+----+--------------------+--------------------+
 id| host_about| host_since|
+----+--------------------+--------------------+
2060| null| 2008-08-18|
2595|A New Yorker sinc...| 2008-09-09|
3831| 2008-12-07|https://www.airbn...|
5099|I'm an artist, wr...| 2009-02-02|
5114|I' an easy going ...| 2009-02-02|
5121| I am an artist(p...| 2009-02-03|
5178|I used to work fo...| 2009-03-03|
5203|Our neighborhood ...| "|
5238|I live in NYC, I ...| 2009-02-07|
5441|I am an educator ...| 2009-02-16|
5552|School psychologi...| 2009-02-22|
5803| iron; everything...| lotions|
6021|Non-licensed Arch...| 2009-03-27|
6090|Hey there Airbnb ...| 2009-04-01|
6848|We love to travel...| 2009-05-06|
6990|Capturing the Ste...| 2009-05-12|
7097|Love tourists and...| 2009-05-17|
7726|Married with 2 ch...| 2009-06-10|
7750|Textile Designer,...| 2009-05-20|
7801|We are a couple i...| 2009-06-12|
+----+--------------------+--------------------+
only showing top 20 rows

Looks like we still have some problem. Out of these 20 rows, rows with ID 3831 and 5803 have some problems.

Lets try to fix this with this logic. Sometimes we have text encoded in double quotes and at that time we want whatever is inside the quotes to be taken as a string skipping all the delimiters and newline characters. This is what we will do here.

In [17]:
# File location and type
file_location = "/FileStore/tables/listings.csv"
file_type = "csv"

# CSV options
infer_schema = "true"
first_row_is_header = "true"
delimiter = ","

# The applied options are for CSV files. For other file types, these will be ignored.
df_listing = spark.read.format(file_type) \
  .option("multiline", "true") \
  .option("quote", "\"") \
  .option("escape", "\"") \
  .option("inferSchema", infer_schema) \
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load(file_location)

display(df_listing)

id listing_url scrape_id last_scraped name summary space description experiences_offered neighborhood_overview notes transit access interaction house_rules thumbnail_url medium_url picture_url xl_picture_url host_id host_url host_name host_since host_location host_about host_response_time host_response_rate host_acceptance_rate host_is_superhost host_thumbnail_url host_picture_url host_neighbourhood host_listings_count host_total_listings_count host_verifications host_has_profile_pic host_identity_verified street neighbourhood neighbourhood_cleansed neighbourhood_group_cleansed city state zipcode market smart_location country_code country latitude longitude is_location_exact property_type room_type accommodates bathrooms bedrooms beds bed_type amenities square_feet price weekly_price monthly_price security_deposit cleaning_fee guests_included extra_people minimum_nights maximum_nights minimum_minimum_nights maximum_minimum_nights minimum_maximum_nights maximum_maximum_nights minimum_nights_avg_ntm maximum_nights_avg_ntm calendar_updated has_availability availability_30 availability_60 availability_90 availability_365 calendar_last_scraped number_of_reviews number_of_reviews_ltm first_review last_review review_scores_rating review_scores_accuracy review_scores_cleanliness review_scores_checkin review_scores_communication review_scores_location review_scores_value requires_license license jurisdiction_names instant_bookable is_business_travel_ready cancellation_policy require_guest_profile_picture require_guest_phone_verification calculated_host_listings_count calculated_host_listings_count_entire_homes calculated_host_listings_count_private_rooms calculated_host_listings_count_shared_rooms reviews_per_month 2060 https://www.airbnb.com/rooms/2060 20200313233810 2020-03-14T00:00:00.000+0000 Modern NYC null Lovely, spacious, sunny 1 BR apartment in 6th Floor elevator building steps from gorgeous Fort Tryon Park/The Cloisters in Manhattan, less than 5 min walk from the A-train, 25-minutes to midtown Manhattan. Neighborhood is quiet, safe and hilly. Fully equipped, all brand new kitchen; king size bed; WiFi and cable; and more. We are looking for responsible renters who don't mind feeding our Maine Coon cat while staying there. Lovely, spacious, sunny 1 BR apartment in 6th Floor elevator building steps from gorgeous Fort Tryon Park/The Cloisters in Manhattan, less than 5 min walk from the A-train, 25-minutes to midtown Manhattan. Neighborhood is quiet, safe and hilly. Fully equipped, all brand new kitchen; king size bed; WiFi and cable; and more. We are looking for responsible renters who don't mind feeding our Maine Coon cat while staying there. none null null null null null null null null https://a0.muscache.com/im/pictures/3755/3f9d31cf_original.jpg?aki_policy=large null 2259 https://www.airbnb.com/users/show/2259 Jenny 2008-08-18T00:00:00.000+0000 US null a few days or more 22% 50% f https://a0.muscache.com/im/users/2259/profile_pic/1259094383/original.jpg?aki_policy=profile_small https://a0.muscache.com/im/users/2259/profile_pic/1259094383/original.jpg?aki_policy=profile_x_medium Washington Heights 0 0 ['reviews'] t f New York, NY, United States Manhattan Washington Heights Manhattan New York NY 10040 New York New York, NY US United States 40.85722 -73.9379 t Other Private room 2 null 1 2 Real Bed {Internet,Wifi} null $100.00 null null null null 1 $0.00 1 730 1 1 730 730 1.0 730.0 4 weeks ago t 30 60 90 365 2020-03-14T00:00:00.000+0000 1 0 2008-09-22T00:00:00.000+0000 2008-09-22T00:00:00.000+0000 80 null null null null null null f null null f f flexible f f 1 0 1 0 0.01 2595 https://www.airbnb.com/rooms/2595 20200313233810 2020-03-14T00:00:00.000+0000 Skylit Midtown Castle Beautiful, spacious skylit studio in the heart of Midtown, Manhattan. STUNNING SKYLIT STUDIO / 1 BED + SINGLE / FULL BATH / FULL KITCHEN / FIREPLACE / CENTRALLY LOCATED / WiFi + APPLE TV / SHEETS + TOWELS - Spacious (500+ft²), immaculate and nicely furnished 

In [18]:
df_listing.select("id", "host_about", "host_since").show()

+----+--------------------+-------------------+
 id| host_about| host_since|
+----+--------------------+-------------------+
2060| null|2008-08-18 00:00:00|
2595|A New Yorker sinc...|2008-09-09 00:00:00|
3831|Laid-back bi-coas...|2008-12-07 00:00:00|
5099|I'm an artist, wr...|2009-02-02 00:00:00|
5114|I' an easy going ...|2009-02-02 00:00:00|
5121| I am an artist(p...|2009-02-03 00:00:00|
5178|I used to work fo...|2009-03-03 00:00:00|
5203|Welcome to family...|2009-02-05 00:00:00|
5238|I live in NYC, I ...|2009-02-07 00:00:00|
5441|I am an educator ...|2009-02-16 00:00:00|
5552|School psychologi...|2009-02-22 00:00:00|
5803|Hello, 
I will b...|2009-03-10 00:00:00|
6021|Non-licensed Arch...|2009-03-27 00:00:00|
6090|Hey there Airbnb ...|2009-04-01 00:00:00|
6848|We love to travel...|2009-05-06 00:00:00|
6990|Capturing the Ste...|2009-05-12 00:00:00|
7097|Love tourists and...|2009-05-17 00:00:00|
7726|Married with 2 ch...|2009-06-10 00:00:00|
7750|Textile Designer,...|2009-05-20 00:00:00|
7801|We are a couple i...|2009-06-12 00:00:00|
+----+--------------------+-------------------+
only showing top 20 rows

Now this looks Good. We can proceed further

In [20]:
# This line is there because when there is a table with same name and we delete that using
# drop command that table's metadata is still there in Hive. SO to avoid that 
# we have this configuration
spark.conf.set("spark.sql.legacy.allowCreatingManagedTableUsingNonemptyLocation", "true")

permanent_table_name = "listing"

df_listing.write.format("parquet").saveAsTable(permanent_table_name)

In [21]:
df_listing.printSchema()

root
-- id: integer (nullable = true)
-- listing_url: string (nullable = true)
-- scrape_id: long (nullable = true)
-- last_scraped: timestamp (nullable = true)
-- name: string (nullable = true)
-- summary: string (nullable = true)
-- space: string (nullable = true)
-- description: string (nullable = true)
-- experiences_offered: string (nullable = true)
-- neighborhood_overview: string (nullable = true)
-- notes: string (nullable = true)
-- transit: string (nullable = true)
-- access: string (nullable = true)
-- interaction: string (nullable = true)
-- house_rules: string (nullable = true)
-- thumbnail_url: string (nullable = true)
-- medium_url: string (nullable = true)
-- picture_url: string (nullable = true)
-- xl_picture_url: string (nullable = true)
-- host_id: integer (nullable = true)
-- host_url: string (nullable = true)
-- host_name: string (nullable = true)
-- host_since: timestamp (nullable = true)
-- host_location: string (nullable = true)
-- host_about: string (nullable = true)
-- host_response_time: string (nullable = true)
-- host_response_rate: string (nullable = true)
-- host_acceptance_rate: string (nullable = true)
-- host_is_superhost: string (nullable = true)
-- host_thumbnail_url: string (nullable = true)
-- host_picture_url: string (nullable = true)
-- host_neighbourhood: string (nullable = true)
-- host_listings_count: integer (nullable = true)
-- host_total_listings_count: integer (nullable = true)
-- host_verifications: string (nullable = true)
-- host_has_profile_pic: string (nullable = true)
-- host_identity_verified: string (nullable = true)
-- street: string (nullable = true)
-- neighbourhood: string (nullable = true)
-- neighbourhood_cleansed: string (nullable = true)
-- neighbourhood_group_cleansed: string (nullable = true)
-- city: string (nullable = true)
-- state: string (nullable = true)
-- zipcode: string (nullable = true)
-- market: string (nullable = true)
-- smart_location: string (nullable = true)
-- country_code: string (nullable = true)
-- country: string (nullable = true)
-- latitude: double (nullable = true)
-- longitude: double (nullable = true)
-- is_location_exact: string (nullable = true)
-- property_type: string (nullable = true)
-- room_type: string (nullable = true)
-- accommodates: integer (nullable = true)
-- bathrooms: double (nullable = true)
-- bedrooms: integer (nullable = true)
-- beds: integer (nullable = true)
-- bed_type: string (nullable = true)
-- amenities: string (nullable = true)
-- square_feet: integer (nullable = true)
-- price: string (nullable = true)
-- weekly_price: string (nullable = true)
-- monthly_price: string (nullable = true)
-- security_deposit: string (nullable = true)
-- cleaning_fee: string (nullable = true)
-- guests_included: integer (nullable = true)
-- extra_people: string (nullable = true)
-- minimum_nights: integer (nullable = true)
-- maximum_nights: integer (nullable = true)
-- minimum_minimum_nights: integer (nullable = true)
-- maximum_minimum_nights: integer (nullable = true)
-- minimum_maximum_nights: integer (nullable = true)
-- maximum_maximum_nights: integer (nullable = true)
-- minimum_nights_avg_ntm: double (nullable = true)
-- maximum_nights_avg_ntm: double (nullable = true)
-- calendar_updated: string (nullable = true)
-- has_availability: string (nullable = true)
-- availability_30: integer (nullable = true)
-- availability_60: integer (nullable = true)
-- availability_90: integer (nullable = true)
-- availability_365: integer (nullable = true)
-- calendar_last_scraped: timestamp (nullable = true)
-- number_of_reviews: integer (nullable = true)
-- number_of_reviews_ltm: integer (nullable = true)
-- first_review: timestamp (nullable = true)
-- last_review: timestamp (nullable = true)
-- review_scores_rating: integer (nullable = true)
-- review_scores_accuracy: integer (nullable = true)
-- review_scores_cleanliness: integer (nullable = true)
-- review_scores_checkin: integer (nullable = true)
-- review_scores_communication: i

Similarly fo Neighbourhoods file

In this case we will see how to set the schema by ourselves

In [23]:
from pyspark.sql.types import *

# File location and type
file_location = "/FileStore/tables/neighbourhoods.csv"
file_type = "csv"

# CSV options
# Infer_schema is false because we want to infer it on our own
infer_schema = "false"
first_row_is_header = "true"
delimiter = ","

# Here we are defining schema one by one for each column
neighbourhood_schema = StructType([
  StructField("neighbourhood_group", StringType(), True),
  StructField("neighbourhood", StringType(), True)
])

# The applied options are for CSV files. For other file types, these will be ignored.
df_neighbourhood = spark.read.format(file_type) \
  .option("wholeFile", "true") \
  .option("multiline", "true") \
  .option("Schema", neighbourhood_schema) \
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load(file_location)

display(df_neighbourhood)

neighbourhood_group neighbourhood Bronx Allerton Bronx Baychester Bronx Belmont Bronx Bronxdale Bronx Castle Hill Bronx City Island Bronx Claremont Village Bronx Clason Point Bronx Concourse Bronx Concourse Village Bronx Co-op City Bronx Country Club Bronx Eastchester Bronx East Morrisania Bronx Edenwald Bronx Fieldston Bronx Fordham Bronx Highbridge Bronx Hunts Point Bronx Kingsbridge Bronx Longwood Bronx Melrose Bronx Morrisania Bronx Morris Heights Bronx Morris Park Bronx Mott Haven Bronx Mount Eden Bronx Mount Hope Bronx North Riverdale Bronx Norwood Bronx Olinville Bronx Parkchester Bronx Pelham Bay Bronx Pelham Gardens Bronx Port Morris Bronx Riverdale Bronx Schuylerville Bronx Soundview Bronx Spuyten Duyvil Bronx Throgs Neck Bronx Tremont Bronx Unionport Bronx University Heights Bronx Van Nest Bronx Wakefield Bronx Westchester Square Bronx West Farms Bronx Williamsbridge Bronx Woodlawn Brooklyn Bath Beach Brooklyn Bay Ridge Brooklyn Bedford-Stuyvesant Brooklyn Bensonhurst Brooklyn Bergen Beach Brooklyn Boerum Hill Brooklyn Borough Park Brooklyn Brighton Beach Brooklyn Brooklyn Heights Brooklyn Brownsville Brooklyn Bushwick Brooklyn Canarsie Brooklyn Carroll Gardens Brooklyn Clinton Hill Brooklyn Cobble Hill Brooklyn Columbia St Brooklyn Coney Island Brooklyn Crown Heights Brooklyn Cypress Hills Brooklyn Downtown Brooklyn Brooklyn DUMBO Brooklyn Dyker Heights Brooklyn East Flatbush Brooklyn East New York Brooklyn Flatbush Brooklyn Flatlands Brooklyn Fort Greene Brooklyn Fort Hamilton Brooklyn Gerritsen Beach Brooklyn Gowanus Brooklyn Gravesend Brooklyn Greenpoint Brooklyn Kensington Brooklyn Manhattan Beach Brooklyn Midwood Brooklyn Mill Basin Brooklyn Navy Yard Brooklyn Park Slope Brooklyn Prospect Heights Brooklyn Prospect-Lefferts Gardens Brooklyn Red Hook Brooklyn Sea Gate Brooklyn Sheepshead Bay Brooklyn South Slope Brooklyn Sunset Park Brooklyn Vinegar Hill Brooklyn Williamsburg Brooklyn Windsor Terrace Manhattan Battery Park City Manhattan Chelsea Manhattan Chinatown Manhattan Civic Center Manhattan East Harlem Manhattan East Village Manhattan Financial District Manhattan Flatiron District Manhattan Gramercy Manhattan Greenwich Village Manhattan Harlem Manhattan Hell's Kitchen Manhattan Inwood Manhattan Kips Bay Manhattan Little Italy Manhattan Lower East Side Manhattan Marble Hill Manhattan Midtown Manhattan Morningside Heights Manhattan Murray Hill Manhattan NoHo Manhattan Nolita Manhattan Roosevelt Island Manhattan SoHo Manhattan Stuyvesant Town Manhattan Theater District Manhattan Tribeca Manhattan Two Bridges Manhattan Upper East Side Manhattan Upper West Side Manhattan Washington Heights Manhattan West Village Queens Arverne Queens Astoria Queens Bayside Queens Bayswater Queens Bay Terrace Queens Belle Harbor Queens Bellerose Queens Breezy Point Queens Briarwood Queens Cambria Heights Queens College Point Queens Corona Queens Ditmars Steinway Queens Douglaston Queens East Elmhurst Queens Edgemere Queens Elmhurst Queens Far Rockaway Queens Flushing Queens Forest Hills Queens Fresh Meadows Queens Glendale Queens Glen Oaks Queens Hollis Queens Hollis Hills Queens Holliswood Queens Howard Beach Queens Jackson Heights Queens Jamaica Queens Jamaica Estates Queens Jamaica Hills Queens Kew Gardens Queens Kew Gardens Hills Queens Laurelton Queens Little Neck Queens Long Island City Queens Maspeth Queens Middle Village Queens Neponsit Queens Ozone Park Queens Queens Village Queens Rego Park Queens Richmond Hill Queens Ridgewood Queens Rockaway Beach Queens Rosedale Queens South Ozone Park Queens Springfield Gardens Queens St. Albans Queens Sunnyside Queens Whitestone Queens Woodhaven Queens Woodside Staten Island Arden Heights Staten Island Arrochar Staten Island Bay Terrace, Staten Island Staten Island Bloomfield Staten Island Bull's Head Staten Island Castleton Corners Staten Island Charleston Staten Island Chelsea, Staten Island Staten Island Clifton Staten Island Concord Staten Island Dongan Hills Staten Island El

In [24]:
permanent_table_name = "neighbourhood"

# to make sure other table with same name is deleted.
df_neighbourhood.write.mode("overwrite").format("parquet").saveAsTable(permanent_table_name)

Now for the last table.

In [26]:
# File location and type
file_location = "/FileStore/tables/reviews.csv"
file_type = "csv"

# CSV options
infer_schema = "true"
first_row_is_header = "true"
delimiter = ","

# The applied options are for CSV files. For other file types, these will be ignored.
df_reviews= spark.read.format(file_type) \
  .option("inferSchema", infer_schema) \
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load(file_location)

display(df_reviews)

listing_id id date reviewer_id reviewer_name comments 2060 158 2008-09-22 2865 Thom "very nice neighborhood,close enough to ""A"" train comfortable bed and clean home over all. null null null null null Jennys cat is very sweet and fun to play with but wants to sleep in bed with you and won't shut up unless such privilages are granted . . . null null null null Meyow meyow meyow." null null null null null 2595 17857 2009-11-21 50679 Jean Notre séjour de trois nuits.
 Nous avons apprécier L'appartement qui est très bien situé. Agréable propre et bien soigné. C'est idéal pour une famille de 3 ou 4 personnes. null null null null Petits soucis en arrivant il y avait personne pour nous recevoir et il manquait le savon pour la douche le liquide vaisselle nous les avons reçu de surlendemain. Il y a aussi le bruit du Métro de NY donc une première nuit difficile si on est pas habitué. Jennifer est correcte le remboursement de la caution était très rapide. A part ces petits détails notre court séjour c'est bien passé. null Si j'ai la possibilité de revenir sur NY pour les vacances je reprendrai à ""The Midtown Castle"" null null null null Jean null null null null null Possession - Ile de La Réunion null null null null null 
 null null null null null 2595 19176 2009-12-05 53267 Cate Great experience. 2595 19760 2009-12-10 38960 Anita I've stayed with my friend at the Midtown Castle for six days and it was a lovely place to be. A big spacious room with a pointy roof, which really makes you feel like staying in a castle. The location is perfect. It is just a few steps from Macy's Time Square and Theatre District. Everything worked just perfect with the keys etc. Thank you so much Jennifer, we had a great time in New York.
 Attention: it's on the 4th floor without a lift :-) but definetely worth it!" null null null null null 2595 34320 2010-04-09 71130 Kai-Uwe We've been staying here for about 9 nights, enjoying to be in the center of the city, that never sleeps...short ways to everywhere in Manhattan, by subway or by walk. Midtown castle is a beauftiful and tastful place, Jennifer and Tori relaxed and friendly hosts - thats why we - the three Berliners - recommand that place! Good to have WiFi and a little kitchen too! 2595 46312 2010-05-25 117113 Alicia We had a wonderful stay at Jennifer's charming apartment! They were very organized and helpful; I would definitely recommend staying at the Midtown Castle! 2595 1238204 2012-05-07 1783688 Sergey Hi to everyone!
 Would say our greatest compliments to Jennifer the host of Midtown Castle. We spent in this lovely apartment in the heart of Manhattan one month (April 2012) and will remember this time as ours best. null null null The apartment is pretty spacious and great located - the 5-th Ave right around the corner. There is everything you can need during your short or long stay. Jennifer is very friendly vigorous and very responsible host. Thanks her and highly recomend this apartment for everyone who are looking for a quiet place right in the center of the boiling Midtown!" null null null null 2595 1293632 2012-05-17 1870771 Loïc Jennifer was very friendly and helpful, and her place is exactly as advertised. The location is very convenient, and it was a pleasure to stay at the Midtown Castle. I definitely recommend it :)
 Thanks !" null null null null null 2595 2022498 2012-08-18 2124102 Melanie This apartment is like a real castle old and unique. The age- related stains on the bathroom floor and dark discolorations in the carpet too indeed indicate that the building was built a long, long time ago. 
 We weren’t happy with the way the apartment was cleaned. Jennifer the host sent in a cleaning lady right the next morning and therefore did everything she thought was appropriate to make our stay comfortable. She let us know that guest satisfaction is important to her. null null null null After we found out that the key for the main entrance was missing by locking ourselves out in the middle of t

Now if you can see then just like first table we have problems with this table too.

Let's try to solve that problem using the same approach.

In [28]:
# File location and type
file_location = "/FileStore/tables/reviews.csv"
file_type = "csv"

# CSV options
infer_schema = "true"
first_row_is_header = "true"
delimiter = ","

# The applied options are for CSV files. For other file types, these will be ignored.
df_reviews= spark.read.format(file_type) \
  .option("wholeFile", "true") \
  .option("multiline", "true") \
  .option("inferSchema", infer_schema) \
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load(file_location)

display(df_reviews)

listing_id id date reviewer_id reviewer_name comments 2060 158 2008-09-22 2865 Thom "very nice neighborhood,close enough to ""A"" train comfortable bed and clean home over all. null null null null null Jennys cat is very sweet and fun to play with but wants to sleep in bed with you and won't shut up unless such privilages are granted . . . null null null null Meyow meyow meyow." null null null null null 2595 17857 2009-11-21 50679 Jean "Notre séjour de trois nuits.
Nous avons apprécier L'appartement qui est très bien situé. Agréable, propre et bien soigné. C'est idéal pour une famille de 3 ou 4 personnes.
Petits soucis en arrivant il y avait personne pour nous recevoir, et il manquait le savon pour la douche, le liquide vaisselle, nous les avons reçu de surlendemain. Il y a aussi le bruit du Métro de NY, donc une première nuit difficile si on est pas habitué. Jennifer est correcte le remboursement de la caution était très rapide. A part ces petits détails notre court séjour c'est bien passé. 
Si j'ai la possibilité de revenir sur NY pour les vacances, je reprendrai à ""The Midtown Castle"" Jean null null null null null Possession - Ile de La Réunion null null null null null "
2595,19176,2009-12-05,53267,Cate,Great experience.
2595,19760,2009-12-10,38960,Anita,"I've stayed with my friend at the Midtown Castle for six days and it was a lovely place to be. A big spacious room with a pointy roof which really makes you feel like staying in a castle. The location is perfect. It is just a few steps from Macy's Time Square and Theatre District. Everything worked just perfect with the keys etc. Thank you so much Jennifer we had a great time in New York. null null null Attention: it's on the 4th floor without a lift :-) but definetely worth it!" null null null null null 2595 34320 2010-04-09 71130 Kai-Uwe We've been staying here for about 9 nights, enjoying to be in the center of the city, that never sleeps...short ways to everywhere in Manhattan, by subway or by walk. Midtown castle is a beauftiful and tastful place, Jennifer and Tori relaxed and friendly hosts - thats why we - the three Berliners - recommand that place! Good to have WiFi and a little kitchen too! 2595 46312 2010-05-25 117113 Alicia We had a wonderful stay at Jennifer's charming apartment! They were very organized and helpful; I would definitely recommend staying at the Midtown Castle! 2595 1238204 2012-05-07 1783688 Sergey Hi to everyone!
Would say our greatest compliments to Jennifer, the host of Midtown Castle. We spent in this lovely apartment in the heart of Manhattan one month (April, 2012) and will remember this time as ours best.
The apartment is pretty spacious and great located - the 5-th Ave right around the corner. There is everything you can need during your short or long stay. Jennifer is very friendly, vigorous and very responsible host. Thanks her and highly recomend this apartment for everyone who are looking for a quiet place right in the center of the boiling Midtown! 2595 1293632 2012-05-17 1870771 Loïc Jennifer was very friendly and helpful, and her place is exactly as advertised. The location is very convenient, and it was a pleasure to stay at the Midtown Castle. I definitely recommend it :)

Thanks ! 2595 2022498 2012-08-18 2124102 Melanie This apartment is like a real castle old and unique. The age- related stains on the bathroom floor and dark discolorations in the carpet too indeed indicate that the building was built a long, long time ago. 
We weren’t happy with the way the apartment was cleaned. Jennifer, the host sent in a cleaning lady right the next morning and therefore did everything she thought was appropriate to make our stay comfortable. She let us know that guest satisfaction is important to her. 
After we found out that the key for the main entrance was missing by locking ourselves out in the middle of the night she was so kind to bring us the missing key within an hour. 
We had to leave the apartment a few days ea

Now if you look closely then this table is little better that last one. There is small improvement.

Look at the 5th row and 6th column in both the tables. In the former table the text of that cell was spilled to next row's first column wheras in the latter the text is in that cell only.

This happened because of multiline=True, but this alone is not suffecient as there are still problems in data. And that is because there are multiple newline characters in text due to which only first newline is handled and the others are treated as start of new row.

Let us try more parameters and see the results.

In [30]:
# File location and type
file_location = "/FileStore/tables/reviews.csv"
file_type = "csv"

# CSV options
infer_schema = "true"
first_row_is_header = "true"
delimiter = ","

# The applied options are for CSV files. For other file types, these will be ignored.
df_reviews= spark.read.format(file_type) \
  .option("wholeFile", "true") \
  .option("multiline", "true") \
  .option("quote", "\"") \
  .option("escape", "\"") \
  .option("inferSchema", infer_schema) \
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load(file_location)

display(df_reviews)

listing_id id date reviewer_id reviewer_name comments 2060 158 2008-09-22T00:00:00.000+0000 2865 Thom very nice neighborhood,close enough to "A" train,
comfortable bed and clean home over all.
Jennys cat is very sweet and fun to play with, but wants to sleep in bed with you and won't shut up unless such privilages are granted . . .
Meyow meyow meyow. 2595 17857 2009-11-21T00:00:00.000+0000 50679 Jean Notre séjour de trois nuits.
Nous avons apprécier L'appartement qui est très bien situé. Agréable, propre et bien soigné. C'est idéal pour une famille de 3 ou 4 personnes.
Petits soucis en arrivant il y avait personne pour nous recevoir, et il manquait le savon pour la douche, le liquide vaisselle, nous les avons reçu de surlendemain. Il y a aussi le bruit du Métro de NY, donc une première nuit difficile si on est pas habitué. Jennifer est correcte le remboursement de la caution était très rapide. A part ces petits détails notre court séjour c'est bien passé. 
Si j'ai la possibilité de revenir sur NY pour les vacances, je reprendrai à "The Midtown Castle"
Jean
Possession - Ile de La Réunion
 2595 19176 2009-12-05T00:00:00.000+0000 53267 Cate Great experience. 2595 19760 2009-12-10T00:00:00.000+0000 38960 Anita I've stayed with my friend at the Midtown Castle for six days and it was a lovely place to be. A big spacious room with a pointy roof, which really makes you feel like staying in a castle. The location is perfect. It is just a few steps from Macy's Time Square and Theatre District. Everything worked just perfect with the keys etc. Thank you so much Jennifer, we had a great time in New York.
Attention: it's on the 4th floor without a lift :-) but definetely worth it! 2595 34320 2010-04-09T00:00:00.000+0000 71130 Kai-Uwe We've been staying here for about 9 nights, enjoying to be in the center of the city, that never sleeps...short ways to everywhere in Manhattan, by subway or by walk. Midtown castle is a beauftiful and tastful place, Jennifer and Tori relaxed and friendly hosts - thats why we - the three Berliners - recommand that place! Good to have WiFi and a little kitchen too! 2595 46312 2010-05-25T00:00:00.000+0000 117113 Alicia We had a wonderful stay at Jennifer's charming apartment! They were very organized and helpful; I would definitely recommend staying at the Midtown Castle! 2595 1238204 2012-05-07T00:00:00.000+0000 1783688 Sergey Hi to everyone!
Would say our greatest compliments to Jennifer, the host of Midtown Castle. We spent in this lovely apartment in the heart of Manhattan one month (April, 2012) and will remember this time as ours best.
The apartment is pretty spacious and great located - the 5-th Ave right around the corner. There is everything you can need during your short or long stay. Jennifer is very friendly, vigorous and very responsible host. Thanks her and highly recomend this apartment for everyone who are looking for a quiet place right in the center of the boiling Midtown! 2595 1293632 2012-05-17T00:00:00.000+0000 1870771 Loïc Jennifer was very friendly and helpful, and her place is exactly as advertised. The location is very convenient, and it was a pleasure to stay at the Midtown Castle. I definitely recommend it :)

Thanks ! 2595 2022498 2012-08-18T00:00:00.000+0000 2124102 Melanie This apartment is like a real castle old and unique. The age- related stains on the bathroom floor and dark discolorations in the carpet too indeed indicate that the building was built a long, long time ago. 
We weren’t happy with the way the apartment was cleaned. Jennifer, the host sent in a cleaning lady right the next morning and therefore did everything she thought was appropriate to make our stay comfortable. She let us know that guest satisfaction is important to her. 
After we found out that the key for the main entrance was missing by locking ourselves out in the middle of the night she was so kind to bring us the missing key within an hour. 
We had to leave the apartment a few days earli

**Problem solved**. Now the data is in good shape using these parameters.

**But** to understand more things we will fix this issue with some different technique

In [32]:
display(spark.read.text("/FileStore/tables/reviews.csv"))

value listing_id,id,date,reviewer_id,reviewer_name,comments 2060,158,2008-09-22,2865,Thom,"very nice neighborhood,close enough to ""A"" train, comfortable bed and clean home over all. Jennys cat is very sweet and fun to play with, but wants to sleep in bed with you and won't shut up unless such privilages are granted . . . Meyow meyow meyow." 2595,17857,2009-11-21,50679,Jean,"Notre séjour de trois nuits. Nous avons apprécier L'appartement qui est très bien situé. Agréable, propre et bien soigné. C'est idéal pour une famille de 3 ou 4 personnes. Petits soucis en arrivant il y avait personne pour nous recevoir, et il manquait le savon pour la douche, le liquide vaisselle, nous les avons reçu de surlendemain. Il y a aussi le bruit du Métro de NY, donc une première nuit difficile si on est pas habitué. Jennifer est correcte le remboursement de la caution était très rapide. A part ces petits détails notre court séjour c'est bien passé. Si j'ai la possibilité de revenir sur NY pour les vacances, je reprendrai à ""The Midtown Castle"" Jean Possession - Ile de La Réunion " 2595,19176,2009-12-05,53267,Cate,Great experience. 2595,19760,2009-12-10,38960,Anita,"I've stayed with my friend at the Midtown Castle for six days and it was a lovely place to be. A big spacious room with a pointy roof, which really makes you feel like staying in a castle. The location is perfect. It is just a few steps from Macy's Time Square and Theatre District. Everything worked just perfect with the keys etc. Thank you so much Jennifer, we had a great time in New York. Attention: it's on the 4th floor without a lift :-) but definetely worth it!" 2595,34320,2010-04-09,71130,Kai-Uwe,"We've been staying here for about 9 nights, enjoying to be in the center of the city, that never sleeps...short ways to everywhere in Manhattan, by subway or by walk. Midtown castle is a beauftiful and tastful place, Jennifer and Tori relaxed and friendly hosts - thats why we - the three Berliners - recommand that place! Good to have WiFi and a little kitchen too!" 2595,46312,2010-05-25,117113,Alicia,We had a wonderful stay at Jennifer's charming apartment! They were very organized and helpful; I would definitely recommend staying at the Midtown Castle! 2595,1238204,2012-05-07,1783688,Sergey,"Hi to everyone! Would say our greatest compliments to Jennifer, the host of Midtown Castle. We spent in this lovely apartment in the heart of Manhattan one month (April, 2012) and will remember this time as ours best. The apartment is pretty spacious and great located - the 5-th Ave right around the corner. There is everything you can need during your short or long stay. Jennifer is very friendly, vigorous and very responsible host. Thanks her and highly recomend this apartment for everyone who are looking for a quiet place right in the center of the boiling Midtown!" 2595,1293632,2012-05-17,1870771,Loïc,"Jennifer was very friendly and helpful, and her place is exactly as advertised. The location is very convenient, and it was a pleasure to stay at the Midtown Castle. I definitely recommend it :) Thanks !" 2595,2022498,2012-08-18,2124102,Melanie,"This apartment is like a real castle old and unique. The age- related stains on the bathroom floor and dark discolorations in the carpet too indeed indicate that the building was built a long, long time ago. We weren’t happy with the way the apartment was cleaned. Jennifer, the host sent in a cleaning lady right the next morning and therefore did everything she thought was appropriate to make our stay comfortable. She let us know that guest satisfaction is important to her. After we found out that the key for the main entrance was missing by locking ourselves out in the middle of the night she was so kind to bring us the missing key within an hour. We had to leave the apartment a few days earlier because we suffered from an allergic reaction (which has never happened before and never after) related to the air conditioner as our doctor told us. The apar

Now if you can see, 2nd to 5th lines should be a single line, but due to multiple newline characters we have this shape where data of same line is spilled to next three lines.

What we are going to do is if a particular row doesnt have a date (a number "/20") we will not take that as a line as its indication that this line is in continuation of last line.

In [34]:
temp_df = spark.read.text("/FileStore/tables/reviews.csv")

In [35]:
header = temp_df.head(1)

In [36]:
fixed_df = temp_df.filter(temp_df.value.contains("/20"))

In [37]:
# As expected there will be unwanted values too. Like first row. There is a /20 text in the comment
# Thats why we have this
display(fixed_df)

value Estación de subte a la vuelta de la esquina, a 15/20 minutos de Manhattan, un barrio hermoso! Sin dudas volveríamos!!!" 14314,224562300,2018-01-03,132749023,Gabriele,"Preis-/ Leistungsverhältnis ist super. Kommunikation mit Jeanne war hervorragend . Der Jahreswechsel 2017/2018 war sehr kalt und Jeanne in Toronto bei ihrer Familie. Sie hat sich immer gemeldet , ob es uns in ihrer Wohnung warm genug sei. Der Empfang war sehr herzlich. Immer wieder gern. That flat is at a really good place - 15/20' walking to Time Square or Central Park, good restaurants and pubs are just nearby, metro station is close as well - > As said : Best Location in NYC :) 23545,1146784,2012-04-18,1132941,Sophie,"nous avons passé un agréable séjour à NYC dans cet appartement (6 personnes) il est superbe ! 2 grandes chambres avec chacune une salle de bain... superbement décoré, nous nous sentions bien, quartier calme dans Harlem à quelques pas d'une station de métro, il faut environ 15/20 mn pour rejoindre Times Square où il y a la correspondance avec pas mal d'autres lignes. Je vous conseille vivement de réserver ce logement pour votre séjour à NYC. Un grand merci à Karen et Norbert qui à notre arrivée avec mis dans le frigo du jus d'orange des (Website hidden by Airbnb) quoi faire notre premier petit déjeuner. c'est sur je reviendrais dans cet appartement." Seth's apartment is pleasant, calm, ideally located in a safe area. A subway station is only a few steps and takes you in the center of Manhattan within 10/15 minutes only. You can also be in the lively and nice areas of Williamsburg (around Bedford and Metropolitan Avenues) within a short time (5 minutes subway or 15/20 minutes walking). which are as valuable as Manhattan and definitely deserve to be explored ! 26012,91265592,2016-08-04,31871141,Viviana,"Wonderful house, very clean and with Everything you need. The neighborhood is very nice, and you have subway to go everywhere in 15/20 minutes. I would recommend it" 31994,8911650,2013-11-25,869597,Jaymie,"We visited the weekend of 11/23-23/2013. Waldemar is a great guy--welcoming and helpful. Our room was large and comfortable--excellent bed and private bathroom. Nice deck outside although it was too chilly to use it. Everything was clean. Cotton sheets. Great Internet connection. We did not use the kitchen but it looked up-to-date and well-equipped. 39267,68280728,2016-04-04,11361108,Clara,"Hôte très sympathique et qui prend du temps pour non seulement nous recevoir (et s'adapte à notre arrivé, perso plus de 19h30/20h) mais aussi de nous donner beaucoup de bons plans !! 39282,214726,2011-04-01,458517,Bárbara,"The room is cosy and very comfortable. The street just below can be a bit noisy but Holly and Gus provide ear plugs for those with a lighter sleep (it didn't bother me much). The neighborhood is incredible: great coffee, tasty bagels, and loads of cute boutique shops. More, the house is perfectly located being close to both the L and the G trains -- about 10/20 min to Manhattan -- and to a nice food store on Union Ave. Gus and Holly are super nice and laid-back, which made me feel at ease in the house. The cats are great too! I would definitely recommend this place to others." 55467,614890865,2020-03-06,78581866,Valerie,We had a great stay at this apartment. Everything (and more) we needed was there. It was only five minutes walk to the metro (20 min to Manhattan center). There was a brunch place next to the metro (Hungry Ghost). The most restaurants (in the center of Williamsburg) were 15/20 minutes walk (you can also take the metro). The neighbourhood was very nice. The apartment is next to a (quiet) park. The communication with Paul was very good. You can send him a message any time and he will reply immediately. There is no reason to choose not for this apartment. 64107,776738,2011-12-11,1394006,Dora,"My boyfriend and I spent 5 nights at Niya's studio and found it nice, spacious,clean, warm and comfortable; the bed is large and the s

In [38]:
fixed_df.count()

Out[60]: 393

In [39]:
final_df = spark.createDataFrame(header).union(fixed_df)

In [40]:
display(final_df)

value listing_id,id,date,reviewer_id,reviewer_name,comments Estación de subte a la vuelta de la esquina, a 15/20 minutos de Manhattan, un barrio hermoso! Sin dudas volveríamos!!!" 14314,224562300,2018-01-03,132749023,Gabriele,"Preis-/ Leistungsverhältnis ist super. Kommunikation mit Jeanne war hervorragend . Der Jahreswechsel 2017/2018 war sehr kalt und Jeanne in Toronto bei ihrer Familie. Sie hat sich immer gemeldet , ob es uns in ihrer Wohnung warm genug sei. Der Empfang war sehr herzlich. Immer wieder gern. That flat is at a really good place - 15/20' walking to Time Square or Central Park, good restaurants and pubs are just nearby, metro station is close as well - > As said : Best Location in NYC :) 23545,1146784,2012-04-18,1132941,Sophie,"nous avons passé un agréable séjour à NYC dans cet appartement (6 personnes) il est superbe ! 2 grandes chambres avec chacune une salle de bain... superbement décoré, nous nous sentions bien, quartier calme dans Harlem à quelques pas d'une station de métro, il faut environ 15/20 mn pour rejoindre Times Square où il y a la correspondance avec pas mal d'autres lignes. Je vous conseille vivement de réserver ce logement pour votre séjour à NYC. Un grand merci à Karen et Norbert qui à notre arrivée avec mis dans le frigo du jus d'orange des (Website hidden by Airbnb) quoi faire notre premier petit déjeuner. c'est sur je reviendrais dans cet appartement." Seth's apartment is pleasant, calm, ideally located in a safe area. A subway station is only a few steps and takes you in the center of Manhattan within 10/15 minutes only. You can also be in the lively and nice areas of Williamsburg (around Bedford and Metropolitan Avenues) within a short time (5 minutes subway or 15/20 minutes walking). which are as valuable as Manhattan and definitely deserve to be explored ! 26012,91265592,2016-08-04,31871141,Viviana,"Wonderful house, very clean and with Everything you need. The neighborhood is very nice, and you have subway to go everywhere in 15/20 minutes. I would recommend it" 31994,8911650,2013-11-25,869597,Jaymie,"We visited the weekend of 11/23-23/2013. Waldemar is a great guy--welcoming and helpful. Our room was large and comfortable--excellent bed and private bathroom. Nice deck outside although it was too chilly to use it. Everything was clean. Cotton sheets. Great Internet connection. We did not use the kitchen but it looked up-to-date and well-equipped. 39267,68280728,2016-04-04,11361108,Clara,"Hôte très sympathique et qui prend du temps pour non seulement nous recevoir (et s'adapte à notre arrivé, perso plus de 19h30/20h) mais aussi de nous donner beaucoup de bons plans !! 39282,214726,2011-04-01,458517,Bárbara,"The room is cosy and very comfortable. The street just below can be a bit noisy but Holly and Gus provide ear plugs for those with a lighter sleep (it didn't bother me much). The neighborhood is incredible: great coffee, tasty bagels, and loads of cute boutique shops. More, the house is perfectly located being close to both the L and the G trains -- about 10/20 min to Manhattan -- and to a nice food store on Union Ave. Gus and Holly are super nice and laid-back, which made me feel at ease in the house. The cats are great too! I would definitely recommend this place to others." 55467,614890865,2020-03-06,78581866,Valerie,We had a great stay at this apartment. Everything (and more) we needed was there. It was only five minutes walk to the metro (20 min to Manhattan center). There was a brunch place next to the metro (Hungry Ghost). The most restaurants (in the center of Williamsburg) were 15/20 minutes walk (you can also take the metro). The neighbourhood was very nice. The apartment is next to a (quiet) park. The communication with Paul was very good. You can send him a message any time and he will reply immediately. There is no reason to choose not for this apartment. 64107,776738,2011-12-11,1394006,Dora,"My boyfriend and I spent 5 nights at Niya's studio and found it nice, spacious,c

In [41]:
final_df.count()

Out[59]: 394

In [42]:
# Some of the rows are good but some still have errors
final_df.show()

+--------------------+
 value|
+--------------------+
listing_id,id,dat...|
Estación de subte...|
14314,224562300,2...|
That flat is at a...|
23545,1146784,201...|
Seth's apartment ...|
26012,91265592,20...|
31994,8911650,201...|
39267,68280728,20...|
39282,214726,2011...|
55467,614890865,2...|
64107,776738,2011...|
74680,3811140,201...|
94477,1326721,201...|
151199,18295974,2...|
151199,110087072,...|
158955,47526496,2...|
For music fans yo...|
195989,29544219,2...|
253623,225150858,...|
+--------------------+
only showing top 20 rows

In [43]:
# Wrritig back this fixed data


# Reason for repartition(1)
# Files are written as map-reduce and multiple part files is created
# So iF we do repartition(1) then only one partition will be there.

final_df.repartition(1).write.text("/FileStore/tables/reviews_fixed")

In [44]:
%sh
ls /dbfs/FileStore/tables

listings.csv
loan.csv
loans_small.csv
neighbourhoods.csv
new.csv
reviews.csv
reviews_fixed

In [45]:
display(dbutils.fs.ls("/FileStore/tables/"))

path name size dbfs:/FileStore/tables/listings.csv listings.csv 193223579 dbfs:/FileStore/tables/loan.csv loan.csv 1189395649 dbfs:/FileStore/tables/loans_small.csv loans_small.csv 85867758 dbfs:/FileStore/tables/neighbourhoods.csv neighbourhoods.csv 4962 dbfs:/FileStore/tables/new.csv new.csv 37 dbfs:/FileStore/tables/reviews.csv reviews.csv 417194617 dbfs:/FileStore/tables/reviews_fixed/ reviews_fixed/ 0

Here as you can see the reviews_fixed is stored as an folder. Lets see inside that

In [47]:
display(dbutils.fs.ls("/FileStore/tables/reviews_fixed/"))

path name size dbfs:/FileStore/tables/reviews_fixed/_SUCCESS _SUCCESS 0 dbfs:/FileStore/tables/reviews_fixed/_committed_6794153250789761477 _committed_6794153250789761477 113 dbfs:/FileStore/tables/reviews_fixed/_started_6794153250789761477 _started_6794153250789761477 0 dbfs:/FileStore/tables/reviews_fixed/part-00000-tid-6794153250789761477-2b987b47-e9c2-4348-bcfa-a18873ef3b17-145-1-c000.txt part-00000-tid-6794153250789761477-2b987b47-e9c2-4348-bcfa-a18873ef3b17-145-1-c000.txt 172848

Now here is the significance of repartition(1). Only one file is there (.txt file). If this was not there then there will be multiple files written in parallel

Since this cleaning was just for demonstration and it still has some problems we will use the older methods to save table in DB as we need cleaned data for other downstream tasks.

In [50]:
# File location and type
file_location = "/FileStore/tables/reviews.csv"
file_type = "csv"

# CSV options
infer_schema = "true"
first_row_is_header = "true"
delimiter = ","

# The applied options are for CSV files. For other file types, these will be ignored.
df_reviews= spark.read.format(file_type) \
  .option("wholeFile", "true") \
  .option("multiline", "true") \
  .option("quote", "\"") \
  .option("escape", "\"") \
  .option("inferSchema", infer_schema) \
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load(file_location)

display(df_reviews)

listing_id id date reviewer_id reviewer_name comments 2060 158 2008-09-22T00:00:00.000+0000 2865 Thom very nice neighborhood,close enough to "A" train,
comfortable bed and clean home over all.
Jennys cat is very sweet and fun to play with, but wants to sleep in bed with you and won't shut up unless such privilages are granted . . .
Meyow meyow meyow. 2595 17857 2009-11-21T00:00:00.000+0000 50679 Jean Notre séjour de trois nuits.
Nous avons apprécier L'appartement qui est très bien situé. Agréable, propre et bien soigné. C'est idéal pour une famille de 3 ou 4 personnes.
Petits soucis en arrivant il y avait personne pour nous recevoir, et il manquait le savon pour la douche, le liquide vaisselle, nous les avons reçu de surlendemain. Il y a aussi le bruit du Métro de NY, donc une première nuit difficile si on est pas habitué. Jennifer est correcte le remboursement de la caution était très rapide. A part ces petits détails notre court séjour c'est bien passé. 
Si j'ai la possibilité de revenir sur NY pour les vacances, je reprendrai à "The Midtown Castle"
Jean
Possession - Ile de La Réunion
 2595 19176 2009-12-05T00:00:00.000+0000 53267 Cate Great experience. 2595 19760 2009-12-10T00:00:00.000+0000 38960 Anita I've stayed with my friend at the Midtown Castle for six days and it was a lovely place to be. A big spacious room with a pointy roof, which really makes you feel like staying in a castle. The location is perfect. It is just a few steps from Macy's Time Square and Theatre District. Everything worked just perfect with the keys etc. Thank you so much Jennifer, we had a great time in New York.
Attention: it's on the 4th floor without a lift :-) but definetely worth it! 2595 34320 2010-04-09T00:00:00.000+0000 71130 Kai-Uwe We've been staying here for about 9 nights, enjoying to be in the center of the city, that never sleeps...short ways to everywhere in Manhattan, by subway or by walk. Midtown castle is a beauftiful and tastful place, Jennifer and Tori relaxed and friendly hosts - thats why we - the three Berliners - recommand that place! Good to have WiFi and a little kitchen too! 2595 46312 2010-05-25T00:00:00.000+0000 117113 Alicia We had a wonderful stay at Jennifer's charming apartment! They were very organized and helpful; I would definitely recommend staying at the Midtown Castle! 2595 1238204 2012-05-07T00:00:00.000+0000 1783688 Sergey Hi to everyone!
Would say our greatest compliments to Jennifer, the host of Midtown Castle. We spent in this lovely apartment in the heart of Manhattan one month (April, 2012) and will remember this time as ours best.
The apartment is pretty spacious and great located - the 5-th Ave right around the corner. There is everything you can need during your short or long stay. Jennifer is very friendly, vigorous and very responsible host. Thanks her and highly recomend this apartment for everyone who are looking for a quiet place right in the center of the boiling Midtown! 2595 1293632 2012-05-17T00:00:00.000+0000 1870771 Loïc Jennifer was very friendly and helpful, and her place is exactly as advertised. The location is very convenient, and it was a pleasure to stay at the Midtown Castle. I definitely recommend it :)

Thanks ! 2595 2022498 2012-08-18T00:00:00.000+0000 2124102 Melanie This apartment is like a real castle old and unique. The age- related stains on the bathroom floor and dark discolorations in the carpet too indeed indicate that the building was built a long, long time ago. 
We weren’t happy with the way the apartment was cleaned. Jennifer, the host sent in a cleaning lady right the next morning and therefore did everything she thought was appropriate to make our stay comfortable. She let us know that guest satisfaction is important to her. 
After we found out that the key for the main entrance was missing by locking ourselves out in the middle of the night she was so kind to bring us the missing key within an hour. 
We had to leave the apartment a few days earli

In [51]:
permanent_table_name = "reviews"

# to make sure other table with same name is deleted.
df_reviews.write.mode("overwrite").format("parquet").saveAsTable(permanent_table_name)

In [52]:
%sql
select * from reviews

listing_id id date reviewer_id reviewer_name comments 2060 158 2008-09-22T00:00:00.000+0000 2865 Thom very nice neighborhood,close enough to "A" train,
comfortable bed and clean home over all.
Jennys cat is very sweet and fun to play with, but wants to sleep in bed with you and won't shut up unless such privilages are granted . . .
Meyow meyow meyow. 2595 17857 2009-11-21T00:00:00.000+0000 50679 Jean Notre séjour de trois nuits.
Nous avons apprécier L'appartement qui est très bien situé. Agréable, propre et bien soigné. C'est idéal pour une famille de 3 ou 4 personnes.
Petits soucis en arrivant il y avait personne pour nous recevoir, et il manquait le savon pour la douche, le liquide vaisselle, nous les avons reçu de surlendemain. Il y a aussi le bruit du Métro de NY, donc une première nuit difficile si on est pas habitué. Jennifer est correcte le remboursement de la caution était très rapide. A part ces petits détails notre court séjour c'est bien passé. 
Si j'ai la possibilité de revenir sur NY pour les vacances, je reprendrai à "The Midtown Castle"
Jean
Possession - Ile de La Réunion
 2595 19176 2009-12-05T00:00:00.000+0000 53267 Cate Great experience. 2595 19760 2009-12-10T00:00:00.000+0000 38960 Anita I've stayed with my friend at the Midtown Castle for six days and it was a lovely place to be. A big spacious room with a pointy roof, which really makes you feel like staying in a castle. The location is perfect. It is just a few steps from Macy's Time Square and Theatre District. Everything worked just perfect with the keys etc. Thank you so much Jennifer, we had a great time in New York.
Attention: it's on the 4th floor without a lift :-) but definetely worth it! 2595 34320 2010-04-09T00:00:00.000+0000 71130 Kai-Uwe We've been staying here for about 9 nights, enjoying to be in the center of the city, that never sleeps...short ways to everywhere in Manhattan, by subway or by walk. Midtown castle is a beauftiful and tastful place, Jennifer and Tori relaxed and friendly hosts - thats why we - the three Berliners - recommand that place! Good to have WiFi and a little kitchen too! 2595 46312 2010-05-25T00:00:00.000+0000 117113 Alicia We had a wonderful stay at Jennifer's charming apartment! They were very organized and helpful; I would definitely recommend staying at the Midtown Castle! 2595 1238204 2012-05-07T00:00:00.000+0000 1783688 Sergey Hi to everyone!
Would say our greatest compliments to Jennifer, the host of Midtown Castle. We spent in this lovely apartment in the heart of Manhattan one month (April, 2012) and will remember this time as ours best.
The apartment is pretty spacious and great located - the 5-th Ave right around the corner. There is everything you can need during your short or long stay. Jennifer is very friendly, vigorous and very responsible host. Thanks her and highly recomend this apartment for everyone who are looking for a quiet place right in the center of the boiling Midtown! 2595 1293632 2012-05-17T00:00:00.000+0000 1870771 Loïc Jennifer was very friendly and helpful, and her place is exactly as advertised. The location is very convenient, and it was a pleasure to stay at the Midtown Castle. I definitely recommend it :)

Thanks ! 2595 2022498 2012-08-18T00:00:00.000+0000 2124102 Melanie This apartment is like a real castle old and unique. The age- related stains on the bathroom floor and dark discolorations in the carpet too indeed indicate that the building was built a long, long time ago. 
We weren’t happy with the way the apartment was cleaned. Jennifer, the host sent in a cleaning lady right the next morning and therefore did everything she thought was appropriate to make our stay comfortable. She let us know that guest satisfaction is important to her. 
After we found out that the key for the main entrance was missing by locking ourselves out in the middle of the night she was so kind to bring us the missing key within an hour. 
We had to leave the apartment a few days earli

# Part 2 - Reading Data

In [54]:
listing_df = spark.table("listing") 
reviews_df = spark.table("reviews")
neighbourhood_df = spark.table("neighbourhood")

In [55]:
display(reviews_df)

listing_id id date reviewer_id reviewer_name comments 2060 158 2008-09-22T00:00:00.000+0000 2865 Thom very nice neighborhood,close enough to "A" train,
comfortable bed and clean home over all.
Jennys cat is very sweet and fun to play with, but wants to sleep in bed with you and won't shut up unless such privilages are granted . . .
Meyow meyow meyow. 2595 17857 2009-11-21T00:00:00.000+0000 50679 Jean Notre séjour de trois nuits.
Nous avons apprécier L'appartement qui est très bien situé. Agréable, propre et bien soigné. C'est idéal pour une famille de 3 ou 4 personnes.
Petits soucis en arrivant il y avait personne pour nous recevoir, et il manquait le savon pour la douche, le liquide vaisselle, nous les avons reçu de surlendemain. Il y a aussi le bruit du Métro de NY, donc une première nuit difficile si on est pas habitué. Jennifer est correcte le remboursement de la caution était très rapide. A part ces petits détails notre court séjour c'est bien passé. 
Si j'ai la possibilité de revenir sur NY pour les vacances, je reprendrai à "The Midtown Castle"
Jean
Possession - Ile de La Réunion
 2595 19176 2009-12-05T00:00:00.000+0000 53267 Cate Great experience. 2595 19760 2009-12-10T00:00:00.000+0000 38960 Anita I've stayed with my friend at the Midtown Castle for six days and it was a lovely place to be. A big spacious room with a pointy roof, which really makes you feel like staying in a castle. The location is perfect. It is just a few steps from Macy's Time Square and Theatre District. Everything worked just perfect with the keys etc. Thank you so much Jennifer, we had a great time in New York.
Attention: it's on the 4th floor without a lift :-) but definetely worth it! 2595 34320 2010-04-09T00:00:00.000+0000 71130 Kai-Uwe We've been staying here for about 9 nights, enjoying to be in the center of the city, that never sleeps...short ways to everywhere in Manhattan, by subway or by walk. Midtown castle is a beauftiful and tastful place, Jennifer and Tori relaxed and friendly hosts - thats why we - the three Berliners - recommand that place! Good to have WiFi and a little kitchen too! 2595 46312 2010-05-25T00:00:00.000+0000 117113 Alicia We had a wonderful stay at Jennifer's charming apartment! They were very organized and helpful; I would definitely recommend staying at the Midtown Castle! 2595 1238204 2012-05-07T00:00:00.000+0000 1783688 Sergey Hi to everyone!
Would say our greatest compliments to Jennifer, the host of Midtown Castle. We spent in this lovely apartment in the heart of Manhattan one month (April, 2012) and will remember this time as ours best.
The apartment is pretty spacious and great located - the 5-th Ave right around the corner. There is everything you can need during your short or long stay. Jennifer is very friendly, vigorous and very responsible host. Thanks her and highly recomend this apartment for everyone who are looking for a quiet place right in the center of the boiling Midtown! 2595 1293632 2012-05-17T00:00:00.000+0000 1870771 Loïc Jennifer was very friendly and helpful, and her place is exactly as advertised. The location is very convenient, and it was a pleasure to stay at the Midtown Castle. I definitely recommend it :)

Thanks ! 2595 2022498 2012-08-18T00:00:00.000+0000 2124102 Melanie This apartment is like a real castle old and unique. The age- related stains on the bathroom floor and dark discolorations in the carpet too indeed indicate that the building was built a long, long time ago. 
We weren’t happy with the way the apartment was cleaned. Jennifer, the host sent in a cleaning lady right the next morning and therefore did everything she thought was appropriate to make our stay comfortable. She let us know that guest satisfaction is important to her. 
After we found out that the key for the main entrance was missing by locking ourselves out in the middle of the night she was so kind to bring us the missing key within an hour. 
We had to leave the apartment a few days earli

In [56]:
display(neighbourhood_df)

neighbourhood_group neighbourhood Bronx Allerton Bronx Baychester Bronx Belmont Bronx Bronxdale Bronx Castle Hill Bronx City Island Bronx Claremont Village Bronx Clason Point Bronx Concourse Bronx Concourse Village Bronx Co-op City Bronx Country Club Bronx Eastchester Bronx East Morrisania Bronx Edenwald Bronx Fieldston Bronx Fordham Bronx Highbridge Bronx Hunts Point Bronx Kingsbridge Bronx Longwood Bronx Melrose Bronx Morrisania Bronx Morris Heights Bronx Morris Park Bronx Mott Haven Bronx Mount Eden Bronx Mount Hope Bronx North Riverdale Bronx Norwood Bronx Olinville Bronx Parkchester Bronx Pelham Bay Bronx Pelham Gardens Bronx Port Morris Bronx Riverdale Bronx Schuylerville Bronx Soundview Bronx Spuyten Duyvil Bronx Throgs Neck Bronx Tremont Bronx Unionport Bronx University Heights Bronx Van Nest Bronx Wakefield Bronx Westchester Square Bronx West Farms Bronx Williamsbridge Bronx Woodlawn Brooklyn Bath Beach Brooklyn Bay Ridge Brooklyn Bedford-Stuyvesant Brooklyn Bensonhurst Brooklyn Bergen Beach Brooklyn Boerum Hill Brooklyn Borough Park Brooklyn Brighton Beach Brooklyn Brooklyn Heights Brooklyn Brownsville Brooklyn Bushwick Brooklyn Canarsie Brooklyn Carroll Gardens Brooklyn Clinton Hill Brooklyn Cobble Hill Brooklyn Columbia St Brooklyn Coney Island Brooklyn Crown Heights Brooklyn Cypress Hills Brooklyn Downtown Brooklyn Brooklyn DUMBO Brooklyn Dyker Heights Brooklyn East Flatbush Brooklyn East New York Brooklyn Flatbush Brooklyn Flatlands Brooklyn Fort Greene Brooklyn Fort Hamilton Brooklyn Gerritsen Beach Brooklyn Gowanus Brooklyn Gravesend Brooklyn Greenpoint Brooklyn Kensington Brooklyn Manhattan Beach Brooklyn Midwood Brooklyn Mill Basin Brooklyn Navy Yard Brooklyn Park Slope Brooklyn Prospect Heights Brooklyn Prospect-Lefferts Gardens Brooklyn Red Hook Brooklyn Sea Gate Brooklyn Sheepshead Bay Brooklyn South Slope Brooklyn Sunset Park Brooklyn Vinegar Hill Brooklyn Williamsburg Brooklyn Windsor Terrace Manhattan Battery Park City Manhattan Chelsea Manhattan Chinatown Manhattan Civic Center Manhattan East Harlem Manhattan East Village Manhattan Financial District Manhattan Flatiron District Manhattan Gramercy Manhattan Greenwich Village Manhattan Harlem Manhattan Hell's Kitchen Manhattan Inwood Manhattan Kips Bay Manhattan Little Italy Manhattan Lower East Side Manhattan Marble Hill Manhattan Midtown Manhattan Morningside Heights Manhattan Murray Hill Manhattan NoHo Manhattan Nolita Manhattan Roosevelt Island Manhattan SoHo Manhattan Stuyvesant Town Manhattan Theater District Manhattan Tribeca Manhattan Two Bridges Manhattan Upper East Side Manhattan Upper West Side Manhattan Washington Heights Manhattan West Village Queens Arverne Queens Astoria Queens Bayside Queens Bayswater Queens Bay Terrace Queens Belle Harbor Queens Bellerose Queens Breezy Point Queens Briarwood Queens Cambria Heights Queens College Point Queens Corona Queens Ditmars Steinway Queens Douglaston Queens East Elmhurst Queens Edgemere Queens Elmhurst Queens Far Rockaway Queens Flushing Queens Forest Hills Queens Fresh Meadows Queens Glendale Queens Glen Oaks Queens Hollis Queens Hollis Hills Queens Holliswood Queens Howard Beach Queens Jackson Heights Queens Jamaica Queens Jamaica Estates Queens Jamaica Hills Queens Kew Gardens Queens Kew Gardens Hills Queens Laurelton Queens Little Neck Queens Long Island City Queens Maspeth Queens Middle Village Queens Neponsit Queens Ozone Park Queens Queens Village Queens Rego Park Queens Richmond Hill Queens Ridgewood Queens Rockaway Beach Queens Rosedale Queens South Ozone Park Queens Springfield Gardens Queens St. Albans Queens Sunnyside Queens Whitestone Queens Woodhaven Queens Woodside Staten Island Arden Heights Staten Island Arrochar Staten Island Bay Terrace, Staten Island Staten Island Bloomfield Staten Island Bull's Head Staten Island Castleton Corners Staten Island Charleston Staten Island Chelsea, Staten Island Staten Island Clifton Staten Island Concord Staten Island Dongan Hills Staten Island El

In [57]:
display(listing_df)

id listing_url scrape_id last_scraped name summary space description experiences_offered neighborhood_overview notes transit access interaction house_rules thumbnail_url medium_url picture_url xl_picture_url host_id host_url host_name host_since host_location host_about host_response_time host_response_rate host_acceptance_rate host_is_superhost host_thumbnail_url host_picture_url host_neighbourhood host_listings_count host_total_listings_count host_verifications host_has_profile_pic host_identity_verified street neighbourhood neighbourhood_cleansed neighbourhood_group_cleansed city state zipcode market smart_location country_code country latitude longitude is_location_exact property_type room_type accommodates bathrooms bedrooms beds bed_type amenities square_feet price weekly_price monthly_price security_deposit cleaning_fee guests_included extra_people minimum_nights maximum_nights minimum_minimum_nights maximum_minimum_nights minimum_maximum_nights maximum_maximum_nights minimum_nights_avg_ntm maximum_nights_avg_ntm calendar_updated has_availability availability_30 availability_60 availability_90 availability_365 calendar_last_scraped number_of_reviews number_of_reviews_ltm first_review last_review review_scores_rating review_scores_accuracy review_scores_cleanliness review_scores_checkin review_scores_communication review_scores_location review_scores_value requires_license license jurisdiction_names instant_bookable is_business_travel_ready cancellation_policy require_guest_profile_picture require_guest_phone_verification calculated_host_listings_count calculated_host_listings_count_entire_homes calculated_host_listings_count_private_rooms calculated_host_listings_count_shared_rooms reviews_per_month 2060 https://www.airbnb.com/rooms/2060 20200313233810 2020-03-14T00:00:00.000+0000 Modern NYC null Lovely, spacious, sunny 1 BR apartment in 6th Floor elevator building steps from gorgeous Fort Tryon Park/The Cloisters in Manhattan, less than 5 min walk from the A-train, 25-minutes to midtown Manhattan. Neighborhood is quiet, safe and hilly. Fully equipped, all brand new kitchen; king size bed; WiFi and cable; and more. We are looking for responsible renters who don't mind feeding our Maine Coon cat while staying there. Lovely, spacious, sunny 1 BR apartment in 6th Floor elevator building steps from gorgeous Fort Tryon Park/The Cloisters in Manhattan, less than 5 min walk from the A-train, 25-minutes to midtown Manhattan. Neighborhood is quiet, safe and hilly. Fully equipped, all brand new kitchen; king size bed; WiFi and cable; and more. We are looking for responsible renters who don't mind feeding our Maine Coon cat while staying there. none null null null null null null null null https://a0.muscache.com/im/pictures/3755/3f9d31cf_original.jpg?aki_policy=large null 2259 https://www.airbnb.com/users/show/2259 Jenny 2008-08-18T00:00:00.000+0000 US null a few days or more 22% 50% f https://a0.muscache.com/im/users/2259/profile_pic/1259094383/original.jpg?aki_policy=profile_small https://a0.muscache.com/im/users/2259/profile_pic/1259094383/original.jpg?aki_policy=profile_x_medium Washington Heights 0 0 ['reviews'] t f New York, NY, United States Manhattan Washington Heights Manhattan New York NY 10040 New York New York, NY US United States 40.85722 -73.9379 t Other Private room 2 null 1 2 Real Bed {Internet,Wifi} null $100.00 null null null null 1 $0.00 1 730 1 1 730 730 1.0 730.0 4 weeks ago t 30 60 90 365 2020-03-14T00:00:00.000+0000 1 0 2008-09-22T00:00:00.000+0000 2008-09-22T00:00:00.000+0000 80 null null null null null null f null null f f flexible f f 1 0 1 0 0.01 2595 https://www.airbnb.com/rooms/2595 20200313233810 2020-03-14T00:00:00.000+0000 Skylit Midtown Castle Beautiful, spacious skylit studio in the heart of Midtown, Manhattan. STUNNING SKYLIT STUDIO / 1 BED + SINGLE / FULL BATH / FULL KITCHEN / FIREPLACE / CENTRALLY LOCATED / WiFi + APPLE TV / SHEETS + TOWELS - Spacious (500+ft²), immaculate and nicely furnished 

**From here on we will see different functions applied to dataframe or to table**

In [59]:
from pyspark.sql.functions import *

# 1. What Property Types are available in Airbnb listing and what is the distribution of those in Descending order?

In [61]:
listing_df.groupBy("property_type").count().orderBy("count", ascending=False).show(5)

+-------------+-----+
property_type|count|
+-------------+-----+
 Apartment|39637|
 House| 4164|
 Townhouse| 1766|
 Condominium| 1716|
 Loft| 1376|
+-------------+-----+
only showing top 5 rows

In [62]:
# Other method with use of "col" function.
listing_df.groupBy("property_type").count().orderBy(col("count").desc()).show(5)

+-------------+-----+
property_type|count|
+-------------+-----+
 Apartment|39637|
 House| 4164|
 Townhouse| 1766|
 Condominium| 1716|
 Loft| 1376|
+-------------+-----+
only showing top 5 rows

In [63]:
# Same results but with sort.
listing_df.groupBy("property_type").count().sort("count", ascending=False).show(5)

+-------------+-----+
property_type|count|
+-------------+-----+
 Apartment|39637|
 House| 4164|
 Townhouse| 1766|
 Condominium| 1716|
 Loft| 1376|
+-------------+-----+
only showing top 5 rows

# 2. What is the average price across each property type?

In [65]:
listing_df.groupBy("property_type").agg({"price":"average"}).show(5)

This is giving Null for average because the "price" column is for string type and not of any numeric type.
We can confirm by below two cells.

In [67]:
listing_df.select("price").dtypes

Out[41]: [('price', 'string')]

In [68]:
listing_df.select("price").show(3)

+-------+
 price|
+-------+
$100.00|
$225.00|
 $89.00|
+-------+
only showing top 3 rows

Due to this dollar sign we have data as string. We will have to clean it.

In [70]:
from pyspark.sql.types import FloatType

def trim_char(string):
  return string.strip("$")

# In order to use this function with Spark SQL we have to register it
# Here we are asking to register this udf(user defined function)
spark.udf.register("trim_funct", trim_char)

# In order to use this function with Spark Dataframe, we have to create a 
# UDF out of it. This is what we are doing
trim_func_udf = udf(trim_char)

In [71]:
listing_df.select("property_type", "price", trim_func_udf("price").cast(FloatType()).alias("price_f")).groupBy("property_type").agg({"price_f":"average"}).show()

+--------------------+------------------+
 property_type| avg(price_f)|
+--------------------+------------------+
 Apartment|135.66915845222107|
 Townhouse|140.37412993039442|
 Resort| 541.6438356164383|
 Farm stay| 70.0|
 Guest suite|109.01891252955083|
 Timeshare| 425.0|
 Dome house| 52.5|
Casa particular (...| 79.33333333333333|
 Camper/RV|100.46666666666667|
 Boutique hotel|222.19298245614036|
 Castle| 172.0|
 Loft|188.24480712166172|
 Guesthouse|126.12345679012346|
 Hostel| 89.45652173913044|
 Lighthouse| 499.5|
 Cave| 183.25|
 Villa|122.44117647058823|
 Aparthotel| 322.5625|
 Other| 159.1157894736842|
 Serviced apartment|241.74040632054175|
+--------------------+------------------+
only showing top 20 rows

In [72]:
# For better display in DataBricks notebook
display(listing_df.select("property_type", "price", trim_func_udf("price").cast(FloatType()).alias("price_f")).groupBy("property_type").agg({"price_f":"average"}))

property_type avg(price_f) Apartment 135.66915845222107 Townhouse 140.37412993039442 Resort 541.6438356164383 Farm stay 70.0 Guest suite 109.01891252955083 Timeshare 425.0 Dome house 52.5 Casa particular (Cuba) 79.33333333333333 Camper/RV 100.46666666666667 Boutique hotel 222.19298245614036 Castle 172.0 Loft 188.24480712166172 Guesthouse 126.12345679012346 Hostel 89.45652173913044 Lighthouse 499.5 Cave 183.25 Villa 122.44117647058823 Aparthotel 322.5625 Other 159.1157894736842 Serviced apartment 241.74040632054175 Earth house 72.85714285714286 Treehouse 44.0 Hotel 205.77580071174378 In-law 40.0 Cottage 175.875 Dorm 38.0 Condominium 193.60142348754448 House 109.30886627906976 Yurt 75.0 Bus 175.5 Island 415.0 Tent 179.4 Train 30.0 Barn 132.5 Tiny house 95.25 Boat 152.57142857142858 Houseboat 381.6666666666667 Bungalow 126.65384615384616 Bed and breakfast 105.86274509803921 Cabin 76.5

# 3. Percentage of listing in Neighbourhood

In [74]:
import pyspark.sql.functions as f
from pyspark.sql.window import Window

In [75]:
listing_df.count()

Out[18]: 50796

In [76]:
listing_df.groupBy("neighbourhood").count().show(5)

+---------------+-----+
 neighbourhood|count|
+---------------+-----+
 The Bronx| 652|
Lighthouse HIll| 1|
 Corona| 68|
 Richmondtown| 1|
 Prince's Bay| 1|
+---------------+-----+
only showing top 5 rows

By using Window function

In [78]:
df_neigh_count = listing_df.groupBy("neighbourhood").count()

# f.col("count") will read each cell in the "count" column row by row
# But the sum("count") needs to take the sum of whole column ate once
# that is where over(Window.partitionBy() is used. It tells to take sum
# of whole column.
df_neigh_count = df_neigh_count.withColumn("percentage", round((f.col("count")/f.sum("count").over(Window.partitionBy()) * 100), 3))

display(df_neigh_count.sort("percentage", ascending=False))

neighbourhood count percentage Brooklyn 10997 21.649 Manhattan 10277 20.232 Queens 3158 6.217 Bedford-Stuyvesant 1860 3.662 Williamsburg 1770 3.485 Harlem 1646 3.24 Midtown 1618 3.185 Bushwick 1032 2.032 Upper East Side 899 1.77 Upper West Side 879 1.73 East Village 781 1.538 Astoria 716 1.41 Crown Heights 702 1.382 The Bronx 652 1.284 Lower East Side 646 1.272 Hell's Kitchen 608 1.197 Chelsea 572 1.126 Flatbush 562 1.106 Midtown East 461 0.908 Washington Heights 452 0.89 Financial District 432 0.85 Jamaica 430 0.847 Greenpoint 430 0.847 West Village 385 0.758 East Harlem 381 0.75 Clinton Hill 352 0.693 Park Slope 318 0.626 Hamilton Heights 300 0.591 Alphabet City 283 0.557 Kips Bay 276 0.543 Chinatown 250 0.492 Flushing 216 0.425 East New York 207 0.408 The Rockaways 200 0.394 Fort Greene 197 0.388 Ridgewood 194 0.382 Sunnyside 190 0.374 East Flatbush 185 0.364 Staten Island 182 0.358 Sunset Park 177 0.348 Lefferts Garden 166 0.327 Soho 145 0.285 Greenwich Village 137 0.27 Murray Hill 128 0.252 Bay Ridge 124 0.244 Elmhurst 123 0.242 Flatiron District 121 0.238 Jackson Heights 118 0.232 Canarsie 118 0.232 Prospect Heights 115 0.226 Long Island City 109 0.215 Nolita 106 0.209 Gowanus 105 0.207 Tribeca 103 0.203 Greenwood Heights 100 0.197 Boerum Hill 96 0.189 Morningside Heights 95 0.187 Woodside 92 0.181 Times Square/Theatre District 92 0.181 Roosevelt Island 87 0.171 Carroll Gardens 85 0.167 Inwood 79 0.156 Sheepshead Bay 77 0.152 Ditmars / Steinway 77 0.152 Gramercy Park 74 0.146 Richmond Hill 69 0.136 Corona 68 0.134 Kensington 64 0.126 Windsor Terrace 63 0.124 Woodhaven 63 0.124 Downtown Brooklyn 63 0.124 Midwood 62 0.122 East Elmhurst 62 0.122 Gravesend 57 0.112 Forest Hills 53 0.104 Maspeth 51 0.1 Mott Haven 44 0.087 Flatlands 42 0.083 Concourse 40 0.079 Wakefield 39 0.077 Brooklyn Navy Yard 38 0.075 Baychester 38 0.075 Brooklyn Heights 37 0.073 Bayside 36 0.071 Rego Park 35 0.069 Red Hook 35 0.069 Bensonhurst 31 0.061 Ozone Park 29 0.057 St. George 29 0.057 Glendale 29 0.057 Tremont 28 0.055 Battery Park City 28 0.055 Brighton Beach 27 0.053 Kew Garden Hills 25 0.049 Soundview 25 0.049 DUMBO 24 0.047 Port Morris 23 0.045 Cobble Hill 23 0.045 South Ozone Park 22 0.043 Highbridge 21 0.041 Bedford Park 20 0.039 West Brighton 20 0.039 Brownsville 20 0.039 Union Square 19 0.037 Middle Village 19 0.037 Kingsbridge Heights 18 0.035 Riverdale 17 0.033 Little Italy 16 0.031 Fordham 16 0.031 Throgs Neck 16 0.031 Borough Park 16 0.031 null 15 0.03 Williamsbridge 15 0.03 Noho 15 0.03 Allerton 15 0.03 Morrisania 14 0.028 Hudson Square 14 0.028 Claremont 14 0.028 City Island 14 0.028 Meatpacking District 14 0.028 Parkchester 14 0.028 Grymes Hill 13 0.026 College Point 13 0.026 Manhattan Beach 13 0.026 Coney Island 13 0.026 Stapleton 13 0.026 Whitestone 13 0.026 Bath Beach 12 0.024 South Beach 12 0.024 Pelham Bay 12 0.024 Concourse Village 11 0.022 Columbia Street Waterfront 11 0.022 Morris Park 11 0.022 Civic Center 10 0.02 Morris Heights 10 0.02 Dyker Heights 10 0.02 Hunts Point 10 0.02 Park Versailles 10 0.02 Crotona 10 0.02 Hillcrest 9 0.018 Bronxdale 9 0.018 Utopia 9 0.018 University Heights 9 0.018 Norwood 9 0.018 Port Richmond 9 0.018 Kingsbridge 9 0.018 Fresh Meadows 9 0.018 Sea Gate 9 0.018 Longwood 9 0.018 Howard Beach 9 0.018 Elm Park 9 0.018 Grasmere 9 0.018 Tompkinsville 8 0.016 Castle Hill 7 0.014 Belmont 7 0.014 Edenwald 7 0.014 Melrose 7 0.014 Bergen Beach 7 0.014 Westchester Village 7 0.014 Mariners Harbor 7 0.014 Marble Hill 6 0.012 South Street Seaport 6 0.012 Lindenwood 6 0.012 Van Nest 5 0.01 Concord 5 0.01 New Springville 5 0.01 Rosebank 5 0.01 Dongan Hills 4 0.008 Eastchester 4 0.008 Grant City 4 0.008 Great Kills 4 0.008 New Dorp Beach 3 0.006 Oakwood 3 0.006 Midland Beach 3 0.006 Mount Eden 3 0.006 Westerleigh 3 0.006 Randall Manor 3 0.006 Country Club 2 0.004 Mill Basin 2 0.004 West Farms 2 0.004 Clifton 2 0.004 Fort Wadsworth 2 0.004 Eltingville 2 0.004 Woodlawn 2 0.004 Annadale 2 0.004 New Brighton 2 0.004 

Without using Window function

In [80]:
# Calculating the sum of all the prices first and storing in "s"
s = df_neigh_count.select("count").agg({"count":"sum"}).first()

# Then creating new column "percentage" with percentage formula and rounding off to 3 digits after decimal
temp_df = df_neigh_count.withColumn("percentage", round(((f.col("count")/s[0]) * 100), 3))

# Sorting in descending order
temp_df.sort("percentage", ascending=False).show(5)

+------------------+-----+----------+
 neighbourhood|count|percentage|
+------------------+-----+----------+
 Brooklyn|10997| 21.649|
 Manhattan|10277| 20.232|
 Queens| 3158| 6.217|
Bedford-Stuyvesant| 1860| 3.662|
 Williamsburg| 1770| 3.485|
+------------------+-----+----------+
only showing top 5 rows

# 4. Join Neighbourhood Table to get neigh_group and plot

**My method**

In [83]:
df_neigh_count.join(neighbourhood_df, on=["neighbourhood"], how="inner").groupBy("neighbourhood_group").count().show()

+-------------------+-----+
neighbourhood_group|count|
+-------------------+-----+
 Queens| 25|
 Brooklyn| 41|
 Staten Island| 33|
 Manhattan| 26|
 Bronx| 36|
+-------------------+-----+

In [84]:
display(df_neigh_count.join(neighbourhood_df, on=["neighbourhood"], how="inner").groupBy("neighbourhood_group").count())

neighbourhood_group count Queens 25 Brooklyn 41 Staten Island 33 Manhattan 26 Bronx 36

Srivatsan's method

In [86]:
nei_group = df_neigh_count.alias("nc").join(neighbourhood_df.alias("ne"), f.col("nc.neighbourhood") == f.col("ne.neighbourhood")).select("nc.*", "ne.neighbourhood_group")

In [87]:
nei_group.show(5)

+-------------+-----+----------+-------------------+
neighbourhood|count|percentage|neighbourhood_group|
+-------------+-----+----------+-------------------+
 Corona| 68| 0.134| Queens|
 Richmondtown| 1| 0.002| Staten Island|
 Prince's Bay| 1| 0.002| Staten Island|
 Mill Basin| 2| 0.004| Brooklyn|
 Westerleigh| 3| 0.006| Staten Island|
+-------------+-----+----------+-------------------+
only showing top 5 rows

**Difference Between OrderBy and Sort**

In distributed computing orderBy will fetch data from all the executers and then do a orderBy. Whereas, Sort will do within individual executers.

So if you are sure your partitions are evenly distributed then you can use sort or else use orderBY

In [89]:
nei_group.sort(desc("percentage")).show(10)

+------------------+-----+----------+-------------------+
 neighbourhood|count|percentage|neighbourhood_group|
+------------------+-----+----------+-------------------+
Bedford-Stuyvesant| 1860| 3.662| Brooklyn|
 Williamsburg| 1770| 3.485| Brooklyn|
 Harlem| 1646| 3.24| Manhattan|
 Midtown| 1618| 3.185| Manhattan|
 Bushwick| 1032| 2.032| Brooklyn|
 Upper East Side| 899| 1.77| Manhattan|
 Upper West Side| 879| 1.73| Manhattan|
 East Village| 781| 1.538| Manhattan|
 Astoria| 716| 1.41| Queens|
 Crown Heights| 702| 1.382| Brooklyn|
+------------------+-----+----------+-------------------+
only showing top 10 rows

# 5. Check for Null or NaN

In [91]:
from pyspark.sql.functions import isnan, when, count, col
display(listing_df.select([count(when(isnan(c) | col(c).isNull(), c)).alias(c) for c in listing_df.columns]))

--------------------------------------------------------------------------- 
 Py4JJavaError Traceback (most recent call last)
 /databricks/spark/python/pyspark/sql/utils.py in deco (*a, **kw) 
 62 try : 
 ---> 63 return f ( * a , ** kw ) 
 64 except py4j . protocol . Py4JJavaError as e : 

 /databricks/spark/python/lib/py4j-0.10.7-src.zip/py4j/protocol.py in get_return_value (answer, gateway_client, target_id, name) 
 327 "An error occurred while calling {0}{1}{2}.\n" . 
 --> 328 format(target_id, ".", name), value)
 329 else : 

 Py4JJavaError : An error occurred while calling o240.select.
: org.apache.spark.sql.AnalysisException: cannot resolve 'isnan(default.listing.`last_scraped`)' due to data type mismatch: argument 1 requires (double or float) type, however, 'default.listing.`last_scraped`' is of timestamp type.;;
'Aggregate [count(CASE WHEN (isnan(cast(id#26 as double)) || isnull(id#26)) THEN id END) AS id#1480L, count(CASE WHEN (isnan(cast(listing_url#27 as double)) || isnull(listing_url#27)) THEN listing_url END) AS listing_url#1482L, count(CASE WHEN (isnan(cast(scrape_id#28L as double)) || isnull(scrape_id#28L)) THEN scrape_id END) AS scrape_id#1484L, count(CASE WHEN (isnan(last_scraped#29) || isnull(last_scraped#29)) THEN last_scraped END) AS last_scraped#1486, count(CASE WHEN (isnan(cast(name#30 as double)) || isnull(name#30)) THEN name END) AS name#1488L, count(CASE WHEN (isnan(cast(summary#31 as double)) || isnull(summary#31)) THEN summary END) AS summary#1490L, count(CASE WHEN (isnan(cast(space#32 as double)) || isnull(space#32)) THEN space END) AS space#1492L, count(CASE WHEN (isnan(cast(description#33 as double)) || isnull(description#33)) THEN description END) AS description#1494L, count(CASE WHEN (isnan(cast(experiences_offered#34 as double)) || isnull(experiences_offered#34)) THEN experiences_offered END) AS experiences_offered#1496L, count(CASE WHEN (isnan(cast(neighborhood_overview#35 as double)) || isnull(neighborhood_overview#35)) THEN neighborhood_overview END) AS neighborhood_overview#1498L, count(CASE WHEN (isnan(cast(notes#36 as double)) || isnull(notes#36)) THEN notes END) AS notes#1500L, count(CASE WHEN (isnan(cast(transit#37 as double)) || isnull(transit#37)) THEN transit END) AS transit#1502L, count(CASE WHEN (isnan(cast(access#38 as double)) || isnull(access#38)) THEN access END) AS access#1504L, count(CASE WHEN (isnan(cast(interaction#39 as double)) || isnull(interaction#39)) THEN interaction END) AS interaction#1506L, count(CASE WHEN (isnan(cast(house_rules#40 as double)) || isnull(house_rules#40)) THEN house_rules END) AS house_rules#1508L, count(CASE WHEN (isnan(cast(thumbnail_url#41 as double)) || isnull(thumbnail_url#41)) THEN thumbnail_url END) AS thumbnail_url#1510L, count(CASE WHEN (isnan(cast(medium_url#42 as double)) || isnull(medium_url#42)) THEN medium_url END) AS medium_url#1512L, count(CASE WHEN (isnan(cast(picture_url#43 as double)) || isnull(picture_url#43)) THEN picture_url END) AS picture_url#1514L, count(CASE WHEN (isnan(cast(xl_picture_url#44 as double)) || isnull(xl_picture_url#44)) THEN xl_picture_url END) AS xl_picture_url#1516L, count(CASE WHEN (isnan(cast(host_id#45 as double)) || isnull(host_id#45)) THEN host_id END) AS host_id#1518L, count(CASE WHEN (isnan(cast(host_url#46 as double)) || isnull(host_url#46)) THEN host_url END) AS host_url#1520L, count(CASE WHEN (isnan(cast(host_name#47 as double)) || isnull(host_name#47)) THEN host_name END) AS host_name#1522L, count(CASE WHEN (isnan(host_since#48) || isnull(host_since#48)) THEN host_since END) AS host_since#1524, count(CASE WHEN (isnan(cast(host_location#49 as double)) || isnull(host_location#49)) THEN host_location END) AS host_location#1526L, ... 82 more fields]
+- SubqueryAlias `default`.`listing`
 +- Relation[id#26,listing_url#27,scrape_id#28L,last_scraped#29,name#30,summary#31,space#32,description#33,experiences_offered#34,neighborhood_overview#35,notes#36,transit#37,access#38,interaction#39,house_rules#40,thum

We are getting this error because the last_scraped column is a timestamp column which is not supported by isnan

In [93]:
listing_df.select("last_scraped").dtypes

Out[35]: [('last_scraped', 'timestamp')]

In [94]:
listing_df.select("last_scraped").show(2)

+-------------------+
 last_scraped|
+-------------------+
2020-03-14 00:00:00|
2020-03-14 00:00:00|
+-------------------+
only showing top 2 rows

#6. How many reviews are there per listing

In [96]:
listing_df.alias("list").join(reviews_df.alias("rev"), col("list.id") == col("rev.listing_id"), how="inner").groupBy("listing_id").count().orderBy("count", ascending=False).show(5)

+----------+-----+
listing_id|count|
+----------+-----+
 32678719| 730|
 9145202| 695|
 903972| 649|
 10101135| 648|
 903947| 638|
+----------+-----+
only showing top 5 rows

# 7. How many listings does not have reviews

In [98]:
listing_df.alias("l").join(reviews_df.alias("r"), col("l.id") == col("r.listing_id"), how = "left").select("l.id", "r.listing_id").filter(col("r.listing_id").isNull()).distinct().count()

Out[73]: 10453

# 8. How many listing have atleast 30 reviews?

In [100]:
reviews_df.groupby("listing_id").count().filter(col("count") > 30).count()

Out[79]: 11208

# 9. Reviewers who have done atleast 30 reviews?

In [102]:
reviews_df.groupBy("reviewer_id").count().filter(col("count") > 30).orderBy("count", ascending=False).show(5)

+-----------+-----+
reviewer_id|count|
+-----------+-----+
 86126627| 107|
 111293458| 104|
 563572| 79|
 71164558| 79|
 63643121| 65|
+-----------+-----+
only showing top 5 rows